# Play with Trajectory_Dataloader class

In [554]:
import os
import pickle
import random
import time
import numpy as np
import torch

In [555]:
DATASET_NAME_TO_NUM = {
    'eth': 0,
    'hotel': 1,
    'zara1': 2,
    'zara2': 3,
    'univ': 4
}

In [556]:
class Object(object):
    pass

args = Object()
args.dataset = 'eth5'
args.test_set = 'eth'
args.save_dir = './output/' + args.test_set + "/"
if not os.path.exists(args.save_dir):
    os.makedirs(args.save_dir)

self = Object()
self.args = args


## 1. Init: train and test directories

In [557]:
if self.args.dataset == 'eth5':

    self.data_dirs = ['../data/eth/univ', '../data/eth/hotel',
                      '../data/ucy/zara/zara01', '../data/ucy/zara/zara02',
                      '../data/ucy/univ/students001', '../data/ucy/univ/students003',
                      '../data/ucy/univ/uni_examples', '../data/ucy/zara/zara03']

    # Data directory where the pre-processed pickle file resides
    self.data_dir = './data'
    skip = [6, 10, 10, 10, 10, 10, 10, 10]

    train_set = [i for i in range(len(self.data_dirs))]

    assert args.test_set in DATASET_NAME_TO_NUM.keys(), 'Unsupported dataset {}'.format(args.test_set)

    args.test_set = DATASET_NAME_TO_NUM[args.test_set]

    if args.test_set == 4 or args.test_set == 5:
        self.test_set = [4, 5]
    else:
        self.test_set = [self.args.test_set]

    for x in self.test_set:
        train_set.remove(x)

    self.train_dir = [self.data_dirs[x] for x in train_set]
    self.test_dir = [self.data_dirs[x] for x in self.test_set]
    self.trainskip = [skip[x] for x in train_set]
    self.testskip = [skip[x] for x in self.test_set]
else:
    raise NotImplementedError

In [558]:
args.test_set

0

In [559]:
self.test_dir

['../data/eth/univ']

In [560]:
self.train_dir

['../data/eth/hotel',
 '../data/ucy/zara/zara01',
 '../data/ucy/zara/zara02',
 '../data/ucy/univ/students001',
 '../data/ucy/univ/students003',
 '../data/ucy/univ/uni_examples',
 '../data/ucy/zara/zara03']

In [561]:
skip

[6, 10, 10, 10, 10, 10, 10, 10]

In [562]:
self.trainskip

[10, 10, 10, 10, 10, 10, 10]

In [563]:
self.testskip

[6]

## 2. Init: Creating pre-processed data from raw data

In [564]:
self.train_data_file = os.path.join(self.args.save_dir, "train_trajectories.cpkl")
self.test_data_file = os.path.join(self.args.save_dir, "test_trajectories.cpkl")
self.train_batch_cache = os.path.join(self.args.save_dir, "train_batch_cache.cpkl")
self.test_batch_cache = os.path.join(self.args.save_dir, "test_batch_cache.cpkl")

print("Creating pre-processed data from raw data.")
self.traject_preprocess('train')
self.traject_preprocess('test')
print("Done.")

Creating pre-processed data from raw data.


AttributeError: 'Object' object has no attribute 'traject_preprocess'

## 3. traject_preprocess(setname)

In [578]:
setname = 'train'

In [579]:
if setname == 'train':
    data_dirs = self.train_dir
    data_file = self.train_data_file
else:
    data_dirs = self.test_dir
    data_file = self.test_data_file
    
all_frame_data = []
valid_frame_data = []
numFrame_data = []

Pedlist_data = []
frameped_dict = []  # peds id contained in a certain frame
pedtrajec_dict = []  # trajectories of a certain ped

# For each dataset
for seti, directory in enumerate(data_dirs):

    file_path = os.path.join(directory, 'true_pos_.csv')
    # Load the data from the csv file
    data = np.genfromtxt(file_path, delimiter=',')
    # Frame IDs of the frames in the current dataset

    Pedlist = np.unique(data[1, :]).tolist()
    numPeds = len(Pedlist)
    # Add the list of frameIDs to the frameList_data
    Pedlist_data.append(Pedlist)
    # Initialize the list of numpy arrays for the current dataset
    all_frame_data.append([])
    # Initialize the list of numpy arrays for the current dataset
    valid_frame_data.append([])
    numFrame_data.append([])
    frameped_dict.append({})
    pedtrajec_dict.append({})

    for ind, pedi in enumerate(Pedlist):
        if ind % 100 == 0:
            print(ind, len(Pedlist))
        # Extract trajectories of one person
        FrameContainPed = data[:, data[1, :] == pedi]
        # Extract peds list
        FrameList = FrameContainPed[0, :].tolist()
        if len(FrameList) < 2: #### COSA SUCCEDE SE HO TRAIETTORIE CON MENO DI 20 FRAMES???
            continue
        # Add number of frames of this trajectory
        numFrame_data[seti].append(len(FrameList))
        # Initialize the row of the numpy array
        Trajectories = []
        # For each ped in the current frame

        for fi, frame in enumerate(FrameList):
            # Extract their x and y positions
            current_x = FrameContainPed[3, FrameContainPed[0, :] == frame][0]
            current_y = FrameContainPed[2, FrameContainPed[0, :] == frame][0]
            # Add their pedID, x, y to the row of the numpy array
            Trajectories.append([int(frame), current_x, current_y])
            if int(frame) not in frameped_dict[seti]:
                frameped_dict[seti][int(frame)] = []
            frameped_dict[seti][int(frame)].append(pedi)
        pedtrajec_dict[seti][pedi] = np.array(Trajectories)

f = open(data_file, "wb")
pickle.dump((frameped_dict, pedtrajec_dict), f, protocol=2)
f.close()

0 389
100 389
200 389
300 389
0 148
100 148
0 204
100 204
200 204
0 415
100 415
200 415
300 415
400 415
0 434
100 434
200 434
300 434
400 434
0 118
100 118
0 137
100 137


In [580]:
file_path

'../data/ucy/zara/zara03/true_pos_.csv'

In [581]:
data[:,0:6]

array([[ 0.    ,  0.    ,  0.    ,  0.    ,  0.    ,  0.    ],
       [ 1.    ,  2.    ,  3.    ,  4.    ,  5.    ,  6.    ],
       [12.775 , 12.375 ,  9.3867,  7.8924,  5.7667,  6.5876],
       [ 7.2791,  7.9235,  7.0643,  6.5393,  7.1837,  6.4199]])

In [582]:
import matplotlib.pyplot as plt

def formatted_time(time_in_sec):
    m = time_in_sec//60
    s = time_in_sec%60
    return f"{m:.0f} min and {s:.0f} sec"

if setname == 'test':

    frames = data[0,:]
    pedestrians = data[1,:]
    X = data[3,:]
    Y = data[2,:]

    print(f"There are {len(set(pedestrians))} unique pedestrians")
    print(f"There are unique {len(set(frames))} frames")
    print(f"First frame is {frames.min()}, last frame is: {frames.max()}")
    print(f"Video approximate length: {formatted_time(frames.max()/25)}")
    print(f"Dimension_2: {X.max() - X.min():.2f}")
    print(f"Dimension_3: {Y.max() - Y.min():.2f}")
    
    if args.test_set in [0, 1]:
        plt.scatter(X,Y,s=2)
        plt.gca().invert_yaxis()
    else:
        plt.scatter(Y,X,s=2)

In [583]:
frameped_dict

[{10: [3.0, 4.0, 5.0, 6.0, 7.0, 8.0],
  20: [3.0, 4.0, 5.0, 6.0, 7.0, 8.0],
  30: [3.0, 4.0, 5.0, 6.0, 7.0, 8.0],
  40: [3.0, 4.0, 5.0, 6.0, 7.0, 8.0],
  50: [3.0, 4.0, 5.0, 6.0, 7.0, 8.0],
  60: [3.0, 4.0, 5.0, 6.0, 8.0],
  70: [3.0, 4.0, 5.0, 6.0, 8.0],
  80: [3.0, 5.0, 6.0, 8.0],
  90: [3.0, 5.0, 6.0, 8.0],
  100: [3.0, 5.0, 6.0, 8.0],
  110: [3.0, 5.0, 6.0, 8.0],
  120: [3.0, 5.0, 6.0, 8.0],
  130: [3.0, 5.0, 6.0, 8.0],
  140: [5.0, 6.0, 8.0],
  150: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0],
  160: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0],
  170: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0],
  180: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0, 14.0, 15.0, 16.0],
  190: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0, 14.0, 15.0, 16.0],
  200: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0, 14.0, 15.0, 16.0],
  210: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0, 14.0, 15.0, 16.0],
  220: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0, 14.0, 15.0, 16.0],
  230: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0, 14.0, 15.0, 16.0],
  240: [5.0, 6.0, 8.0, 11.0, 12.0, 13.0, 14.0, 15.0, 16.0, 17.

In [584]:
pedtrajec_dict

[{3.0: array([[ 1.0000e+01, -4.1351e+00,  1.9383e+00],
         [ 2.0000e+01, -3.4862e+00,  1.5317e+00],
         [ 3.0000e+01, -2.9931e+00,  1.1374e+00],
         [ 4.0000e+01, -2.4592e+00,  8.4973e-01],
         [ 5.0000e+01, -1.9978e+00,  4.4133e-01],
         [ 6.0000e+01, -1.5283e+00,  1.6933e-01],
         [ 7.0000e+01, -9.7149e-01, -1.0209e-01],
         [ 8.0000e+01, -3.9081e-01, -3.4554e-01],
         [ 9.0000e+01,  1.8706e-01, -5.4413e-01],
         [ 1.0000e+02,  7.3707e-01, -7.6760e-01],
         [ 1.1000e+02,  1.2078e+00, -9.3552e-01],
         [ 1.2000e+02,  1.7958e+00, -1.1852e+00],
         [ 1.3000e+02,  2.1950e+00, -1.4659e+00]]),
  4.0: array([[10.     , -1.7705 ,  2.7638 ],
         [20.     , -1.0687 ,  2.7291 ],
         [30.     , -0.42651,  2.7243 ],
         [40.     ,  0.34497,  2.7185 ],
         [50.     ,  0.93612,  2.6255 ],
         [60.     ,  1.6747 ,  2.5873 ],
         [70.     ,  2.2651 ,  2.5365 ]]),
  5.0: array([[ 10.     ,   0.92758,  -1.5855 ],


## Init: Load the processed trajs from the pickle file

In [577]:
# Load the processed data from the pickle file
print("Preparing data batches.")
if not (os.path.exists(self.train_batch_cache)):
    self.frameped_dict, self.pedtraject_dict = self.load_dict(self.train_data_file)
    self.dataPreprocess('train')
if not (os.path.exists(self.test_batch_cache)):
    self.test_frameped_dict, self.test_pedtraject_dict = self.load_dict(self.test_data_file)
    self.dataPreprocess('test')

self.trainbatch, self.trainbatchnums, _, _ = self.load_cache(self.train_batch_cache)
self.testbatch, self.testbatchnums, _, _ = self.load_cache(self.test_batch_cache)
print("Done.")

print('Total number of training batches:', self.trainbatchnums)
print('Total number of test batches:', self.testbatchnums)

self.reset_batch_pointer(set='train', valid=False)
self.reset_batch_pointer(set='train', valid=True)
self.reset_batch_pointer(set='test', valid=False)

Preparing data batches.


AttributeError: 'Object' object has no attribute 'load_dict'